# Music Charts

In this example, we will extract information about music charts from tables on Wikipedia.
We will populate the Wikidata predicate "charted in" ([P2291](https://www.wikidata.org/wiki/Property:P2291)), which often occurs with the qualifiers "point in time" ([P585](https://www.wikidata.org/wiki/Property:P585)) and "ranking" ([P1352](https://www.wikidata.org/wiki/Property:P1352)).

In [1]:
from rdflib.plugins.stores.sparqlstore import SPARQLStore
st = SPARQLStore('http://query.wikidata.org/sparql')
r = st.query("""
SELECT DISTINCT ?entity ?article WHERE {
    ?entity wdt:P2291 ?label .
    ?article schema:about ?entity .
    ?article schema:isPartOf <https://en.wikipedia.org/>.
}
""")
ent_abouturl = [tuple(b[v] for v in r.vars) for b in r.bindings]
len(ent_abouturl)

/export/scratch1/home/kruit/venv2/lib/python3.7/site-packages/SPARQLWrapper/Wrapper.py:880: UserWarning: keepalive support not available, so the execution of this method has no effect
  warnings.warn("keepalive support not available, so the execution of this method has no effect")


435

In [4]:
import takco
sample = 1
pages = takco.extract.WikiPages(ent_abouturl[:2]).load()
extracted = list(takco.extract.extract_tables(pages))
takco.preview(extracted)

In [5]:
reshaped = list(takco.TableSet.reshape(extracted, unpivot_heuristics=[takco.reshape.NumSuffix()]))
print(f"Processed {len(list(reshaped))} tables")
takco.preview(reshaped, nrows=5, ntables=25)

Processed 10 tables


In [81]:
import pandas as pd
import json
from takco.table import Table

for t, a in json.load(open('pivot-annotation-precision.json')):
    if not 'level' in t['pivot']:
        continue
        
    t['tableData'] = [[{'text':f'col{i}'} for i in range(len(t['tableHeaders'][0]))]]
    level, colfrom, colto = t['pivot']['level'], t['pivot']['colfrom'], t['pivot']['colto']
    t = Table(t)
    display.display(t.df.takco.highlight_pivot(level, colfrom, colto))
    display.display(t.unpivot(level, colfrom, colto).df.takco)
    print('--')
    
    


--


--


--


--


--


...

--


--


--


--


--


In [61]:
import pandas as pd
t = extracted[0]
hs = takco.reshape.NumSuffix()
for p in hs.find_longest_pivots(t.head):
    head = t.head[:0] + tuple(zip(*hs.split_header(t.head[p.level], p.colfrom, p.colto))) + t.head[1:]
    
    mi = pd.MultiIndex.from_arrays(head)
    df = pd.DataFrame(t.body, columns=mi)
    df = df.melt([mi[1][1]], col_level=1)
    display.display(df.head(3))

AttributeError: 'Table' object has no attribute 'head'

In [4]:
clustered = takco.TableSet.cluster(reshaped, addcontext = ["pgTitle"], matchers=[])

print(f"Processed {len(list(clustered))} tables")
takco.preview(clustered, nrows=5, ntables=25)

Processed 16 tables


In [5]:
linked = takco.TableSet.link(
    clustered, 
    lookup_cells=False, 
    linker_config = {}, 
    lookup_config = {
        'class': 'SQLiteWikiLookup',
        'sqlitedb': '../../data/wdid_wpname.sqlitedb',
        'baseuri': 'http://www.wikidata.org/entity/',
        'fallback': {'class': 'MediaWikiAPI'},
    }
)

print(f"Processed {len(list(linked))} tables")
takco.preview(linked, nrows=5, ntables=25)

Processed 16 tables


In [8]:
searcher_config = {
    'class': "RDFSearcher",
    'encoding': "wikidata",
    'typeProperties': ["http://www.wikidata.org/prop/direct/P31"],
    'statementURIprefix': "http://www.wikidata.org/entity/statement/",
    'store': {
        'class': "HDTStore",
        'path': "/export/scratch1/home/kruit/scratch/downloads/wikidata/wikidata20200309.hdt",
    }
}
typer_config = {
    "class": "EntityType", 
    "db": searcher_config, 
    "type_prop": "http://www.wikidata.org/prop/direct/P31",
    "cover_threshold": 0.2,
}
integrated = takco.TableSet.integrate(linked, pfd_threshold = 0.95, searcher_config=searcher_config, typer_config=typer_config)
print(f"Processed {len(list(integrated))} tables")

integrated_sorted = sorted(integrated, key=lambda table: -table.get('numDataRows', 0))
takco.preview(integrated_sorted, nrows=5, ntables=25)

Processed 16 tables


In [12]:
triples = takco.TableSet.triples(integrated)
print(f"Extracted {sum(len(table.get('triples')) for table in triples)} triples")

Extracted 2749 triples
